# Vermont corridor population chart

In [1]:
import os

import altair
import geopandas

altair.data_transformers.disable_max_rows()

/home/ian/miniconda3/envs/gis/lib/python3.8/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.9.1dev-CAPI-1.14.1) is incompatible with the GEOS version PyGEOS was compiled with (3.9.1-CAPI-1.14.2). Conversions between both will be slow.
  warnings.warn(


DataTransformerRegistry.enable('default')

### Conditionally download OSM and census block data:

In [2]:
if not os.path.exists("socal-latest-free.shp.zip"):
    import requests
    resp = requests.get("http://download.geofabrik.de/north-america/us/california/socal-latest-free.shp.zip")
    with open("socal-latest-free.shp.zip", "wb") as f:
        f.write(resp.content)

In [3]:
if not os.path.exists("census-blocks-2010.shp.zip"):
    import requests
    resp = requests.get("https://opendata.arcgis.com/datasets/e801df58a2874fad8f3c04824a08de22_3.zip")
    with open("census-blocks-2010.shp.zip", "wb") as f:
        f.write(resp.content)

### Select Vermont Avenue from the data

In [4]:
socal_roads = geopandas.read_file(
    "socal-latest-free.shp.zip",
    bbox=(-118.3, 34.12, -118.28, 33.77),
    layer="gis_osm_roads_free_1",
)

/home/ian/miniconda3/envs/gis/lib/python3.8/site-packages/geopandas/geodataframe.py:577: RuntimeWarning: Sequential read of iterator was interrupted. Resetting iterator. This can negatively impact the performance.
  for feature in features_lst:


In [5]:
vermont = socal_roads[
    socal_roads.name.str.lower().str.contains("vermont avenue") &
    socal_roads.name.notna()
]

In [6]:
FEET_PER_MILE = 5280.
SOCAL_FEET = 2229 # California state plane coordinate system in feet
WGS84 = 4326 # WGS84 coordinate system (lat/lon)

In [7]:
vermont_feet = vermont.to_crs(epsg=SOCAL_FEET).unary_union.buffer(200)

### Read in census data

In [8]:
blocks = geopandas.read_file("census-blocks-2010.shp.zip")

In [9]:
blocks = blocks.to_crs(epsg=SOCAL_FEET)
#blocks.geometry=blocks.geometry.simplify(100)

### Join census data with Vermont

In [10]:
blocks_near_vermont = (
    blocks
    [blocks.intersects(vermont_feet.buffer(FEET_PER_MILE))]
    .assign(**{
        "Population density (pop/sqmi)": lambda x: x.POP_2010/(x.area/FEET_PER_MILE/FEET_PER_MILE),
        "distance": lambda x: x.distance(vermont_feet)
    })
    .to_crs(epsg=WGS84)
    .filter(
        ["POP_2010", "Population density (pop/sqmi)", "distance", "COMM", "geometry"]
    ).rename(columns={"POP_2010": "Population","COMM": "Community"})
)

/home/ian/miniconda3/envs/gis/lib/python3.8/site-packages/pygeos/measurement.py:58: RuntimeWarning: overflow encountered in distance
  return lib.distance(a, b, **kwargs)


### Construct chart

In [11]:
slider = altair.binding_range(min=0, max=FEET_PER_MILE, step=250, name='Distance from Vermont Avenue (ft):')
selector = altair.selection_single(
    name="cutoff",
    bind=slider,
    init={'cutoff': 1000}
)

In [12]:
vermont_chart = altair.Chart(vermont.unary_union).mark_geoshape(
    stroke="maroon",
    strokeWidth=3,
    fillOpacity=0,
)

In [13]:
text_chart = altair.Chart(blocks_near_vermont).mark_text(
    fontSize=16, lineBreak='\n', align='left'
).transform_filter(
    altair.datum.distance <= selector.cutoff
).transform_aggregate(
    total="sum(Population)"
).transform_calculate(
    label="'Total population within \\n' + format(cutoff.cutoff, ',') + ' feet: ' + format(datum.total, ',')"
).encode(
    x=altair.value(5),
    y=altair.value(5),
    text="label:N",
)

In [14]:
block_chart = altair.Chart(blocks_near_vermont).mark_geoshape().encode(
    color=altair.condition(
        altair.datum.distance <= selector.cutoff,
        altair.Color("Population density (pop/sqmi):Q", scale=altair.Scale(domain=[0,100_000])),
        altair.ColorValue('lightgray'),
    ),
    tooltip=[
        "Community",
        altair.Tooltip("Population", format=","),
        altair.Tooltip("Population density (pop/sqmi)", format=",.0f"),
    ],
)


chart = altair.layer(
    block_chart,
    vermont_chart,
    text_chart
).add_selection(
    selector
).configure_view(
    stroke=None
).properties(
    width=200,
    height=1000,
)

chart

alt.LayerChart(...)

In [15]:
chart.save("../articles/transit/images/vermont.json")